In [0]:
import pandas as pd
from collections import OrderedDict

In [0]:
ws_code_name_dict = spark.sql('select distinct int(wholesaler_pay_code) as payercode,  wholesaler_name as payername from budtech_brewdat_prod_ods.abi_cloud_wholesaler_ws_wholesaler').toPandas().set_index('payercode')
ws_code_name_dict = dict(ws_code_name_dict['payername'])

In [0]:
def get_one_ws_indics(one_ws_inv, payercode, brand, expire_month):
    in_stw_df = one_ws_inv.loc['STW(+)', :]  
    # in_stw_df = one_ws_inv.loc['STW(+)', :][:-(expire_month + 1)]   # 最后1+inv_expire_month不看，因为没过期呢，也不需要参与分母计算
    total_in_stw = in_stw_df.sum()  # 分母，进货的量  total_stw
    balance_df_at_last = one_ws_inv.iloc[2:-1, -1]   # 最后一个月所有stw分别的库存，包括期初库存
    expired_balance_df = balance_df_at_last[:-(expire_month + 1)]
    write_off_stw = expired_balance_df.sum()    #分子
    write_off_amt_prct = write_off_stw / total_in_stw if total_in_stw > 0 else None          # write off的量 / 进货的量
    write_off_month_cnt = expired_balance_df[expired_balance_df > 0].shape[0]
    has_stw_month = len(in_stw_df[in_stw_df > 0])
    write_off_month_prct = write_off_month_cnt / has_stw_month if has_stw_month > 0 else None
    valid_balance_df = balance_df_at_last[-(expire_month + 1):]
    valid_stw_balance = valid_balance_df.sum()
    # 保存数据
    if not ws_index_dict['ws_name']:
        ws_index_dict['ws_name'] = ws_code_name_dict.get(payercode)
    ws_index_dict.update(dict(payercode=payercode, total_in_stw=total_in_stw, write_off_stw=write_off_stw, write_off_amt_prct=write_off_amt_prct, 
                                write_off_month_cnt=write_off_month_cnt, 
                                has_stw_month=has_stw_month,
                                write_off_month_prct=write_off_month_prct))
    ws_index_dict['year_month'] = '2024-10' 
    return ws_index_dict

In [0]:
expire_month = 9
result = spark.read.parquet(f'/mnt/srf/fifo_inventory_details_month{expire_month}')
result = result.toPandas()
# 暂时填充下all brand的月份
result['expire_month'] = result['expire_month'].apply(lambda x: int(x) if not pd.isna(x) else expire_month)
result = result[result['ws_code'].notnull()]

In [0]:
index_set = result[['ws_code', 'brand', 'expire_month', 'ws_name', 'bu', 'region']].drop_duplicates()
all_result = []
for i in range(len(index_set)):
    ws_index_dict = OrderedDict(index_set.iloc[i])
    payercode = ws_index_dict['ws_code']
    brand = ws_index_dict['brand']
    expire_month = ws_index_dict['expire_month']
    one_ws_inv = result.query('(ws_code == @payercode) & (brand == @brand) & (expire_month == @expire_month)').drop(['ws_code', 'brand', 'expire_month', 'ws_name', 'bu', 'region'], axis=1).set_index('index')
    one_ws_result = get_one_ws_indics(one_ws_inv, payercode, brand, expire_month)
    all_result.append(one_ws_result)
all_result_df = pd.DataFrame(all_result)

In [0]:
all_result_df.display()

ws_code brand expire_month ws_name bu region payercode total_in_stw write_off_stw write_off_amt_prct write_off_month_cnt has_stw_month write_off_month_prct year_month 30011157 BUD 9 福州津烨贸易有限公司 东南区|BU_SE 福建东部|Region_Fujian_East 30011157 34098.5867456 0.0 0.0 0 44 0.0 2024-10 30011157 HBI 9 福州津烨贸易有限公司 东南区|BU_SE 福建东部|Region_Fujian_East 30011157 0.0 0.0 null 0 0 null 2024-10 30011157 HBO 9 福州津烨贸易有限公司 东南区|BU_SE 福建东部|Region_Fujian_East 30011157 0.0 0.0 null 0 0 null 2024-10 30011157 HKOW 9 福州津烨贸易有限公司 东南区|BU_SE 福建东部|Region_Fujian_East 30011157 0.0 0.0 null 0 0 null 2024-10 30011157 ISP 9 福州津烨贸易有限公司 东南区|BU_SE 福建东部|Region_Fujian_East 30011157 10952.48624 0.0 0.0 0 38 0.0 2024-10 30011157 all 12 福州津烨贸易有限公司 东南区|BU_SE 福建东部|Region_Fujian_East 30011157 45051.0729856 0.0 0.0 0 45 0.0 2024-10 30008590 BUD 9 宝清县百畅饮食品有限公司 东北|BU_NE 黑龙江东区|Region_Heilongjiang_East 30008590 53395.490000000005 0.0 0.0 0 47 0.0 2024-10 30008590 HBI 9 宝清县百畅饮食品有限公司 东北|BU_NE 黑龙江东区|Region_Heilongjiang_East 30008590 5901.856800000001 157.62600000000026 0.02670786590416769 6 46 0.13043478260869565 2024-10 30008590 HBO 9 宝清县百畅饮食品有限公司 东北|BU_NE 黑龙江东区|Region_Heilongjiang_East 30008590 42998.414 0.0 0.0 0 47 0.0 2024-10 30008590 HKOW 9 宝清县百畅饮食品有限公司 东北|BU_NE 黑龙江东区|Region_Heilongjiang_East 30008590 99.78999999999999 66.526 0.6666599859705381 2 3 0.6666666666666666 2024-10 30008590 ISP 9 宝清县百畅饮食品有限公司 东北|BU_NE 黑龙江东区|Region_Heilongjiang_East 30008590 3.24 0.0 0.0 0 1 0.0 2024-10 30008590 all 12 宝清县百畅饮食品有限公司 东北|BU_NE 黑龙江东区|Region_Heilongjiang_East 30008590 102398.79079999999 99.73600000000026 9.739958765216227E-4 3 47 0.06382978723404255 2024-10 30020302 BUD 9 常德兆科贸易有限公司 东南区|BU_SE 湖南|Region_Hunan 30020302 29062.149999999998 0.0 0.0 0 20 0.0 2024-10 30020302 HBI 9 常德兆科贸易有限公司 东南区|BU_SE 湖南|Region_Hunan 30020302 19800.289999999997 0.0 0.0 0 18 0.0 2024-10 30020302 HBO 9 常德兆科贸易有限公司 东南区|BU_SE 湖南|Region_Hunan 30020302 19556.1 0.0 0.0 0 19 0.0 2024-10 30020302 HKOW 9 常德兆科贸易有限公司 东南区|BU_SE 湖南|Region_Hunan 30020302 4239.1 0.0 0.0 0 20 0.0 2024-10 30020302 ISP 9 常德兆科贸易有限公司 东南区|BU_SE 湖南|Region_Hunan 30020302 3765.37 0.0 0.0 0 20 0.0 2024-10 30020302 all 12 常德兆科贸易有限公司 东南区|BU_SE 湖南|Region_Hunan 30020302 76423.01 0.0 0.0 0 20 0.0 2024-10 30018261 BUD 9 广州君宇恒达贸易有限公司 南区|BU_S 广东大广州|Region_Guangdong_Greater Guan 30018261 148793.36352 0.0 0.0 0 46 0.0 2024-10 30018261 HBI 9 广州君宇恒达贸易有限公司 南区|BU_S 广东大广州|Region_Guangdong_Greater Guan 30018261 45234.268 0.0 0.0 0 45 0.0 2024-10 30018261 HBO 9 广州君宇恒达贸易有限公司 南区|BU_S 广东大广州|Region_Guangdong_Greater Guan 30018261 0.0 0.0 null 0 0 null 2024-10 30018261 HKOW 9 广州君宇恒达贸易有限公司 南区|BU_S 广东大广州|Region_Guangdong_Greater Guan 30018261 0.0 0.0 null 0 0 null 2024-10 30018261 ISP 9 广州君宇恒达贸易有限公司 南区|BU_S 广东大广州|Region_Guangdong_Greater Guan 30018261 7853.664000000001 0.0 0.0 0 41 0.0 2024-10 30018261 all 12 广州君宇恒达贸易有限公司 南区|BU_S 广东大广州|Region_Guangdong_Greater Guan 30018261 201881.29551999999 0.0 0.0 0 46 0.0 2024-10 30020538 BUD 9 唐山市泊如贸易有限公司 北区|BU_N 河北北区|Region_Hebei_North 30020538 8798.24 0.0 0.0 0 12 0.0 2024-10 30020538 HBI 9 唐山市泊如贸易有限公司 北区|BU_N 河北北区|Region_Hebei_North 30020538 0.0 0.0 null 0 0 null 2024-10 30020538 HBO 9 唐山市泊如贸易有限公司 北区|BU_N 河北北区|Region_Hebei_North 30020538 0.0 0.0 null 0 0 null 2024-10 30020538 HKOW 9 唐山市泊如贸易有限公司 北区|BU_N 河北北区|Region_Hebei_North 30020538 0.0 0.0 null 0 0 null 2024-10 30020538 ISP 9 唐山市泊如贸易有限公司 北区|BU_N 河北北区|Region_Hebei_North 30020538 0.0 0.0 null 0 0 null 2024-10 30020538 all 12 唐山市泊如贸易有限公司 北区|BU_N 河北北区|Region_Hebei_North 30020538 8798.24 0.0 0.0 0 12 0.0 2024-10 30009802 BUD 9 黑山县田氏哈尔滨啤酒经销处 东北|BU_NE 辽西南区|Region_Liaoning_Southwest 30009802 11044.237618399999 0.0 0.0 0 47 0.0 2024-10 30009802 HBI 9 黑山县田氏哈尔滨啤酒经销处 东北|BU_NE 辽西南区|Region_Liaoning_Southwest 30009802 11100.787199999999 0.0 0.0 0 45 0.0 2024-10 30009802 HBO 9 黑山县田氏哈尔滨啤酒经销处 东北|BU_NE 辽西南区|Region_Liaoning_Southwest 30009802 95412.0692 0.0 0.0 0 47 0.0 2024-10 30009802 HKOW 9 黑山县田氏哈尔滨啤酒经销处 东北|BU_NE 辽西南区|Region_Liaoning_Southwest 30009802 304.85 0.0020000000000379714 6.560603575653506E-6 2 6 0

In [0]:
payercode = 30011101
brand = 'HKOW'
expire_month = 9
one_ws_inv = result.query('(ws_code == @payercode) & (brand == @brand) & (expire_month == @expire_month)').drop(['ws_code', 'brand', 'expire_month', 'ws_name', 'bu', 'region'], axis=1).set_index('index')


In [0]:
one_ws_inv.reset_index().display()

index Openning Balance month_1 month_2 month_3 month_4 month_5 month_6 month_7 month_8 month_9 month_10 month_11 month_12 month_13 month_14 month_15 month_16 month_17 month_18 month_19 month_20 month_21 month_22 month_23 month_24 month_25 month_26 month_27 month_28 month_29 month_30 month_31 month_32 month_33 month_34 month_35 month_36 month_37 month_38 month_39 month_40 month_41 month_42 month_43 month_44 month_45 month_46 STW(+) 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 STR(-) null 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 48.33 0.0 5.9399999999999995 1.17 2.16 0.99 48.42 7.6499999999999995 1.3499999999999999 27.9 19.71 67.05 25.56 0.18 1.26 -2.25 -3.33 6.39 7.739999999999999 49.41 97.74 113.49 54.449999999999996 81.72 3.15 18.09 0.44999999999999996 openning_balance null 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 1_STW_balance null 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 2_STW_balance null null 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 3_STW_balance null null null 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 4_STW_balance null null null null 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 5_STW_balance null null null null null 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 6_STW_balance null null null null null null 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 7_STW_balance null null null null null null null 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 8_STW_balance null null null null null null null null 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 9_STW_balance null null null null null null null null null 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 10_STW_balance null null null null null null null null null null 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 11_STW_balance null null null null null null null null null null null 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 12_STW_balance null null null null null null null null null null null null 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 13_STW_balance null null null null null null null null null null null null null 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 14_STW_balance null null null null null null null null null null null null null null 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.